In [1]:
import argparse
import copy
import json
from matplotlib import pyplot as plt
import numpy as np
import pandas as pd
import plotly.express as px

from cadCAD.configuration import Experiment
from cadCAD.configuration.utils import config_sim
from cadCAD.engine import ExecutionContext, ExecutionMode, Executor
from cadCAD import configs

from simulation import (CommonsSimulationConfiguration, bootstrap_simulation,
                        partial_state_update_blocks)

In [2]:
DATA_PATH = './data'

### Plotting methods

In [3]:
def print_plot(df_, param_name, param_values, state_var):
    ax = None
    N = len(param_values)
    for i in range(N):
        ax = df_[df_['simulation']==i].plot('timestep', state_var,
                                              grid=True,
                                              legend = (ax == None),
                                              figsize=(12,6),
                                              ax = ax
                                      )
    ax.legend([f'{param_name}={p}' for p in param_values])


def print_subplots(df_, param_name, param_values, state_var, threshold_mult=1):
    N = len(param_values)
    half = int(np.ceil(N / 2))
    _, axs = plt.subplots(2, half, sharex=True, figsize=(30,6))
    print(N, np.size(axs))
    axs_ = np.reshape(axs, np.size(axs))
    for i in range(N):
        temp = df_[df_['simulation']==i].copy().reset_index(drop=True)

        criteria = temp[state_var].max()
        criteria_idx = temp[state_var].idxmax()
        threshold = threshold_mult * temp[state_var].std()  # STD threshold
        

        temp.plot('timestep', state_var, grid=True, ax=axs_[i])
        # temp[state_var].rolling(window=15).mean().plot(ax=axs_[i])
        
        temp[f'max_diff_{state_var}'] = temp[state_var] - temp[state_var].max()
        temp[f'mean_diff_{state_var}'] = temp[state_var] - temp[state_var].mean()
        temp[f'std_diff_{state_var}'] = temp[state_var] - temp[state_var].std()
        temp['game_over'] = (criteria - temp[state_var]) > (threshold)

        total_gover_points = temp[temp.game_over].loc[criteria_idx:].shape[0]
        
        temp.plot('timestep', f'std_diff_{state_var}', ax=axs_[i])
        axs_[i].scatter([temp[state_var].idxmax()], [temp[state_var].max()], marker='o', c='red')
        axs_[i].plot([criteria_idx] * 20, np.arange(1, step=0.05), c='red')
        temp[temp.game_over].loc[criteria_idx:].plot(kind='scatter', x='timestep', y=state_var, ax=axs_[i], c='black')
        axs_[i].legend([f'{param_name}={param_values[i]}', 
                        # '15D MAvg', 
                        'STD Diff', 
                        f'Peak {state_var} (day={criteria_idx})', 
                        f"max={'%.4f' % criteria}", 
                        f"Game over (c={threshold_mult}*STD) (-{total_gover_points}pts)"
                        ])
        # axs_[i].legend([f'{param_name}={param_values[i]}'])



In [4]:
def custom_legend(fig, labels):
    for i, dat in enumerate(fig.data):
        for elem in dat:
            if elem == 'name':
                fig.data[i].name = labels[int(fig.data[i].name)]
    return fig


In [5]:
def print_pyplot(df, var_names, param_name, labels):
    fig = px.line(
        df,
        x='timestep',
        y=var_names,
        color='simulation',
        labels={'simulation': param_name}
    )
    fig = custom_legend(fig, labels=dict(enumerate(labels)))
    fig.show()    

## System parameters

In [6]:
default_params = dict(hatchers=100,
                      proposals=5,
                      hatch_tribute=0.40,
                      max_proposal_request=0.48,
                      days_to_80p_of_max_voting_weight=30,
                      exit_tribute=0.25,
                      vesting_80p_unlocked=60,  # default
                      kappa=2,  # defauilt
                      timesteps_days=360,
                      random_seed=42
             )
default_params

{'hatchers': 100,
 'proposals': 5,
 'hatch_tribute': 0.4,
 'max_proposal_request': 0.48,
 'days_to_80p_of_max_voting_weight': 30,
 'exit_tribute': 0.25,
 'vesting_80p_unlocked': 60,
 'kappa': 2,
 'timesteps_days': 360,
 'random_seed': 42}

In [7]:
grid_params = [{
        'name': 'hatchers',
        'values': list(range(10, 151, 10))
    }, {
        'name': 'proposals',
        'values': list(range(5, 51, 5))

    }, {
        'name': 'hatch_tribute',
        'values': np.arange(0.1, 1, 0.1).tolist()
    }, {
        'name': 'max_proposal_request',
        'values': np.arange(0.1, 1, 0.1).tolist()
    }, {
        'name': 'days_to_80p_of_max_voting_weight',
        'values': np.arange(15, 100, 15).tolist()
    }, {
        'name': 'exit_tribute',
        'values': np.arange(0.05, 0.5, 0.05).tolist()

    }
]

# Sensitivity Analysis

In [8]:
cache = {}

## One-at-a-time

### Funding pool

In [9]:
for param in grid_params:
    df = pd.read_csv(f"{DATA_PATH}/{param['name']}.csv") 
#     print_plot(df, param['name'], param['values'], 'funding_pool')
    print_pyplot(df, ['funding_pool'], param['name'], param['values'])
    cache[param['name']] = df

### Token Price

In [10]:
for param in grid_params:
#     df = pd.read_csv(f"{DATA_PATH}/{param['name']}.csv") 
    df = cache[param['name']]
#     print_plot(df, param['name'], param['values'], 'funding_pool')
    print_pyplot(df, ['token_price'], param['name'], param['values'])

### Average Sentiment

In [11]:
for param in grid_params:
#     df = pd.read_csv(f"{DATA_PATH}/{param['name']}.csv")
    df = cache[param['name']]
#     print_plot(df, param['name'], param['values'], 'funding_pool')
    print_pyplot(df, ['sentiment'], param['name'], param['values'])

## Score Analysis

In [12]:
dfs = []
for param in grid_params:
    df_ = pd.read_csv(f"{DATA_PATH}/{param['name']}_network_metrics.csv")
    df_['param'] = param['name']
    dfs.append(df_)
    
df_metrics = pd.concat(dfs)
df_metrics.head()

simulation  participants  candidates  funds_candidates  actives  \
0           0            24           0          0.000000        4   
1           1            28           1      76041.549373        1   
2           2            37           0          0.000000        0   
3           3            47           0          0.000000        0   
4           4            67           0          0.000000        1   

   funds_actives  completed  funds_completed  failed  funds_failed     param  
0  116632.013346         56     1.725582e+06      54  1.996106e+06  hatchers  
1   71929.331911         43     2.740508e+06      53  3.525228e+06  hatchers  
2       0.000000         38     2.962369e+06      61  5.352440e+06  hatchers  
3       0.000000         43     5.432381e+06      60  6.361379e+06  hatchers  
4   43487.343143         50     8.257338e+06      38  5.607402e+06  hatchers

### Scoring functions

In [13]:
class CommonsScore(object):
    
    def __init__(self, params, df_raw, metrics):
        self.params = params
        self.df_raw = df_raw
        self.metrics = metrics

    def calc_price_ratio(self):
        '''
            price compared to hatch price
        '''
        hatch_price = self.df_raw.iloc[0, :]['token_price']
        final_price = self.df_raw.iloc[-1, :]['token_price']
        return final_price / hatch_price

    def calc_avg_price_to_initial_ratio(self):
        '''
            Average price compared with hatch price
        '''
        hatch_price = self.df_raw.iloc[0, :]['token_price']
        avg_price = self.df_raw['token_price'].mean()
        return avg_price / hatch_price

    def calc_final_sentinment(self):
        '''
            Sentiment at the end of the 3 years
        '''
        return self.df_raw.iloc[-1, :]['sentiment']

    def calc_funded_proposals_ratio(self):
        '''
            Number of proposals funded compared to initial proposals
        '''
        init_proposals = self.params['proposals']
        funded = self.metrics.candidates + self.metrics.actives + self.metrics.completed + self.metrics.failed
        return funded / init_proposals

    def calc_funds_spent_ratio(self):
        '''
            Total spent by the funding pool compared to the amount received in the hatch phase
        '''
        hatch_funds = self.df_raw.iloc[0,:]['funding_pool']
        total_spent = self.metrics.funds_candidates + self.metrics.funds_actives + self.metrics.funds_completed + self.metrics.funds_failed
        return total_spent / hatch_funds

    def calc_avg_funds_to_initial_ratio(self):
        '''
            Average amount in funding pool over time compared to the amount received in the hatch phase
        '''
        hatch_funds = self.df_raw.iloc[0,:]['funding_pool']
        avg_funds = self.df_raw['funding_pool'].mean()
        return avg_funds / hatch_funds

    def calc_avg_sentiment(self):
        '''
            Average sentiment
        '''
        return self.df_raw['sentiment'].mean()

    def calc_success_to_failed_ratio(self):
        '''
            Ratio of successful projects to failed ones
        '''
        return self.metrics.completed / self.metrics.failed

    def calc_participant_to_hatchers_ratio(self):
        '''
            No of final participants compared to Nº of hatchers
        '''
        hatchers = self.params['hatchers']
        return self.metrics.participants / hatchers
    
    def run(self):
        '''
            Run all score metrics
        '''
        methods = [attr for attr in dir(self) if callable(getattr(self, attr)) and attr.startswith('calc_')] 
        return { method.replace('calc_', ''): getattr(self, method)() for method in methods }
    

### Testing Scoring Strategies

In [14]:
df_scores = df_metrics.copy()

In [15]:
for param in grid_params:
    print(param['name'])
    df_ = cache[param['name']]
    for i in range(len(param['values'])):
        print(f'\t{i}')
        data = df_[df_['simulation'] == i]
        idx = (df_scores.simulation == i) & (df_scores.param == param['name'])
    
        sim_params = copy.deepcopy(default_params)
        sim_params[param['name']] = param['values'][i]
        
        metrics = df_metrics[idx].iloc[0,:]
        
        c_score = CommonsScore(params=sim_params, df_raw=data, metrics=metrics)
        
        score = c_score.run()
        
        for metric, value in score.items():            
            print(f'\t\t{metric}:', value)
            df_scores.loc[idx, metric] = value

hatchers
	0
		avg_funds_to_initial_ratio: 0.5390824646262078
		avg_price_to_initial_ratio: 1.1908835025689317
		avg_sentiment: 0.8281226914987264
		final_sentinment: 0.8557905810146412
		funded_proposals_ratio: 22.8
		funds_spent_ratio: 1.8448606451153762
		participant_to_hatchers_ratio: 2.4
		price_ratio: 1.4041367598327132
		success_to_failed_ratio: 1.037037037037037
	1
		avg_funds_to_initial_ratio: 0.6200553016236913
		avg_price_to_initial_ratio: 0.955299746297667
		avg_sentiment: 0.7129140824693322
		final_sentinment: 0.6347548999465685
		funded_proposals_ratio: 19.6
		funds_spent_ratio: 1.7516044678800455
		participant_to_hatchers_ratio: 1.4
		price_ratio: 0.5713849750317849
		success_to_failed_ratio: 0.8113207547169812
	2
		avg_funds_to_initial_ratio: 0.5708357389099007
		avg_price_to_initial_ratio: 0.6881546920891382
		avg_sentiment: 0.6302574173139408
		final_sentinment: 0.6828629704847742
		funded_proposals_ratio: 19.8
		funds_spent_ratio: 1.579810971580846
		participant_to_ha

		avg_funds_to_initial_ratio: 0.6767187380584445
		avg_price_to_initial_ratio: 0.5269338136231865
		avg_sentiment: 0.535750564302048
		final_sentinment: 0.5733380448257268
		funded_proposals_ratio: 17.0
		funds_spent_ratio: 1.452400366176754
		participant_to_hatchers_ratio: 1.04
		price_ratio: 0.4437378290885731
		success_to_failed_ratio: 0.8409090909090909
	1
		avg_funds_to_initial_ratio: 0.6919364432409668
		avg_price_to_initial_ratio: 0.7303449912254248
		avg_sentiment: 0.628355723364347
		final_sentinment: 0.4991475591111469
		funded_proposals_ratio: 16.0
		funds_spent_ratio: 1.5016755208261234
		participant_to_hatchers_ratio: 1.08
		price_ratio: 0.3453682677944508
		success_to_failed_ratio: 1.0526315789473684
	2
		avg_funds_to_initial_ratio: 0.6466570256430545
		avg_price_to_initial_ratio: 0.8864356957884131
		avg_sentiment: 0.7174209876100137
		final_sentinment: 0.6404210044719986
		funded_proposals_ratio: 16.6
		funds_spent_ratio: 1.4431506199249668
		participant_to_hatchers_rat

In [16]:
df_scores

simulation  participants  candidates  funds_candidates  actives  \
0            0            24           0      0.000000e+00        4   
1            1            28           1      7.604155e+04        1   
2            2            37           0      0.000000e+00        0   
3            3            47           0      0.000000e+00        0   
4            4            67           0      0.000000e+00        1   
5            5            69           2      3.957708e+05        1   
6            6            78           0      0.000000e+00        2   
7            7            88           0      0.000000e+00        0   
8            8            98           1      1.472275e+05        1   
9            9           112           2      1.397868e+05        1   
10          10           123           1      1.427492e+05        0   
11          11           132           0      0.000000e+00        2   
12          12           137           0      0.000000e+00        0   
13          13           145           0      0.000000e+00        0   
14          14           163           2      7.759238e+05        2   
0            0           108           1      6.603796e+04        0   
1            1           115           2      3.211511e+05        3   
2            2           107           1      6.845395e+04        2   
3            3           109           2      3.493543e+05        0   
4            4           110           2      3.847316e+05        1   
5            5           113           0      0.000000e+00        3   
6            6           112           1      2.606514e+05        2   
7            7           106           0      0.000000e+00        1   
8            8           108           3      5.287139e+05        0   
9            9           109           1      6.894681e+04        2   
0            0           110           1      1.083960e+05        1   
1            1           107           2      4.503137e+05        2   
2            2           109           0      0.000000e+00        2   
3            3           108           1      6.603796e+04        0   
4            4           109           2      5.887807e+05        3   
5            5           105           1      6.997507e+05        1   
6            6           109           1      7.294262e+05        1   
7            7           109           2      6.133523e+05        1   
8            8           108           1      2.138145e+05        2   
0            0           104           3      1.109467e+06        1   
1            1           108           1      4.566705e+05        1   
2            2           119           1      1.441779e+05        3   
3            3           105           0      0.000000e+00        0   
4            4           106           0      0.000000e+00        1   
5            5           104           0      0.000000e+00        1   
6            6           109           2      1.593002e+05        2   
7            7           107           1      1.958156e+05        1   
8            8           110           1      6.221238e+04        3   
0            0           105           1      3.269591e+04        1   
1            1           108           1      6.603796e+04        0   
2            2           109           2      5.497463e+05        2   
3            3           106           2      5.800538e+05        1   
4            4           110           1      6.724503e+05        1   
5            5           104           0      0.000000e+00        1   
0            0           102           1      8.823999e+04        1   
1            1           110           3      2.707035e+05        1   
2            2           110           0      0.000000e+00        0   
3            3           111           0      0.000000e+00        2   
4            4           108           1      6.603796e+04        0   
5            5           108           1      7.446442e+04        0   
6            6           108